# Modeling a Double Pendulum
By Marion Madanguit and Nicola van Moon

In [4]:
# Configure Jupyter so figures appear in the notebook
%matplotlib inline

# Configure Jupyter to display the assigned value after an assignment
%config InteractiveShell.ast_node_interactivity='last_expr_or_assign'

# import functions from the modsim.py module
from modsim import *

In [5]:
m = UNITS.meter
s = UNITS.second
minute = UNITS.minute
day = UNITS.day
kg = UNITS.kilogram

degree = UNITS.degree
radian = UNITS.radian

<Unit('radian')>

In [5]:
t_0 = 0 * s
t_end = (2 * minute).to_base_units()
dt = 1 * s

params = Params(L1=1 * m, #length of the inner rod
                L2=1 * m, #length of the outer rod
                angle1 = (90 * degree).to_base_units(), #angle to the left from the vertical of the first rod
                angle2=(90 * degree).to_base_units(), #angle from the vertical of the second rod
"""BEWARE FUTURE NICOLA AND MARION: Later assumptions for simplicity in the initial model depend on this angle being 90 degrees so that would have to be changed before the angle is changed"""
                m1=1 * kg, #mass of the inner rod
                m2=1 * kg, #mass of the outer rod
                v1_init=0 * m / s, #velocity of the inner mass
                v3_init=0 * m / s, #velocity of the outer mass (in reference to the origin) 
                #for simplicity as we test our model we are using 0 initial velocity at the beguining
                g = 9.8 * m / s**2,
                t_end=t_end, dt=dt)

SyntaxError: invalid syntax (<ipython-input-5-7f7ebc9839c7>, line 10)

In [23]:
def pol_vector(mag, angle):
    x, y = pol2cart(angle, mag)
    return Vector(x, y)

In [6]:
def make_system(params):

    """
    make_system creates a system to store the parameters and initial conditions.

    Parameters:
        params: model parameters
    """
    
    # make the initial state
    R1 = pol_vector(params.L1, params.angle1)
    R2 = pol_vector(params.L2, params.angle2)
    R3 = R1 + R2 #R3 is the position of mass 1 in reference to the origin
    V1_angle = Vector(R1.y, R1.x).angle #defines the angle of the inner mass's velocity as perpendicular to it's position vector
    V3_angle = Vector(R3.y, R3.x).angle
    V1 = pol_vector(params.v1_init, V1_angle) #velocity vector of mass 1
    V3 = pol_vector(params.v3_init, V3_angle) #velocity vector of mass 2 in reference to the origin
    
    AT1 = params.g #the tangential acceleration at the beguining of the simulation is just gravity because we are setting the initial angle to be 90 degrees so that the pendulul is horizantal
    AT3 = params.g
    
    """ we are very purposefully starting it at 90 degrees so that we know the initial tangential acceleration so that we can use it to know the Angular acceleration at the beguining which lets us solve for acceleration. In each timestep we will update the tangential acceleration in the state so that we can use it in the next timestep """
    
    init = State(R1=R1, R3=R3, V1=V1, V3=V3, AT1=AT1, AT3=AT3)

    return System(params, init=init)

system = make_system(params)
system.init

NameError: name 'params' is not defined

R1      [6.123233995736766e-17 meter, 1.0 meter]
R3     [1.2246467991473532e-16 meter, 2.0 meter]
V1      [0.0 meter / second, 0.0 meter / second]
V3      [0.0 meter / second, 0.0 meter / second]
AT1                      9.8 meter / second ** 2
AT3                      9.8 meter / second ** 2
dtype: object

In [1]:
def slope_func(state, t, system):

    """
    slope_func calculates the derivative of each state variable.

    Parameters:
        state: a state variable containing the position vectors, velocity vectors, and tangential acceleration vectors
        t: the time step
        system: the system storing the parameters and initial conditions
    """

    R1, R3, V1, V2, AT1, AT3 = state
    m1, m2, g = system.m1, system.m2, system.g
    L1, L2 = system.l1, system.l2

    alpha1 = AT1 / R1.mag
    alpha3 = AT3 / R3.mag

    T1 = (-m1 * L2 * alpha2) / sin(R2.angle - R1.angle)
    T2 = (-m1 * L1 * alpha1 + g * sin(R1.angle)) / sin(R2.angle - R1.angle)

    dRdt1 = V1
    dRdt3 = V2

    dVdt1 = (-T1 * ((R1) / R1.mag)) + T2 * (((R3-R1) / (R3-R1).mag) + m1 * g) / m1
    dVdt3 = (-T2 * ((R3-R1) / (R3-R1).mag) + m2 * g) / m2

    return dRdt1, dRdt3, dVdt1, dVdt3

In [2]:
slope_func(system.init, 0, system)

NameError: name 'system' is not defined

In [3]:
def event_func(state, t, system):

    return system.t_end - t

In [4]:
results, details = run_ode_solver(system, slope_func, events=event_func)
details

NameError: name 'run_ode_solver' is not defined